# Imports

In [1]:
# Matplotlib
from matplotlib.path import Path
from matplotlib import pyplot as plt
from matplotlib import patches as patches
from matplotlib.backends.backend_agg import FigureCanvasAgg as FigureCanvas

# Shapely
from shapely.geometry import *
from shapely.affinity import *
from shapely.affinity import rotate as rotate_
from shapely.ops import unary_union

# Numpy
import numpy as np
from numpy.linalg import norm
from numpy.random import choice, rand, randn, randint

# Vsketch
import vsketch

# Etc
from noise import pnoise2

# Drawing functions

In [2]:
def circle(c = (0, 0), r = 1):
    return Point(c).buffer(r)

def ribbon(
    x = 0,
    y = 0,
    reflect_horizontal = False,
    reflect_vertical = False,
    rotate = False,
    d = .2
    ):
    # Build shape
    part1 = circle((-d, 0)).difference((circle((+d, 0))))
    part1 = part1.difference(Polygon([(-1-d, 0), (-1-d, 1), (1, 1), (1, 0)]))
    part1 = part1.union(Polygon([(-1-d, 0), (-1-d, 1), (-1+d, 1), (-1+d, 0)]))
    part2 = circle((-d, 0)).symmetric_difference((circle((+d, 0))))
    part2 = part2.difference(Polygon([(-1+d, 0), (-1+d, 1), (1+d, 1), (1+d, 0)]))
    part2 = part2.difference(part1)
    shape = MultiPolygon([part1, part2])

    # Translate, reflect, rotate
    shape = translate(shape, x, y)
    if reflect_horizontal:
        shape = scale(shape, -1, 1)
    if reflect_vertical:
        shape = scale(shape, 1, -1)
    if rotate:
        shape = rotate_(shape, 180)

    return shape

def shape2patches(shape, **kwargs):
    
    if type(shape) != MultiPolygon:
        shape = [shape]

    for s in shape:
        try: s = s.exterior;
        except: pass;
        
        yield patches.Polygon(list(zip(*s.xy)), **kwargs)

# Matplotlib

In [10]:
# For reproducbility
np.random.seed(5)

palette = [
    '#E4572E',
    '#F3A712',
    '#A8C686'
]

# Params
ribbon_offset = .2
shadow_offset = (-.1, -.1)
rotation_angle = 5

# Define set of shapes
Δ = ribbon_offset
shapes = [
    ribbon(x = 0, y = +0-Δ), 
    ribbon(x = 2, y = +0+Δ, rotate = True), 
    ribbon(x = 4, y = -2-Δ),
    ribbon(x = 4, y = -2+0, rotate = True, reflect_horizontal = True), 
    ribbon(x = 2, y = -4-0, rotate = True, reflect_vertical = True), 
    ribbon(x = 2, y = -3+Δ, rotate = True, reflect_horizontal = True), 
    ribbon(x = 2, y = -3+0), 
    ribbon(x = 2, y = -1+Δ, rotate = True, reflect_horizontal = True), 
    ribbon(x = 0, y = -2+Δ, rotate = True, reflect_horizontal = True)
]

# Rotate shapes
shapes = [rotate(shape, rotation_angle) for shape in shapes]
all_shapes = unary_union(shapes)

# Compute shadow
shadow = translate(all_shapes, *shadow_offset).difference(all_shapes)

fig, ax = plt.subplots(figsize = (10, 10))
plt.tight_layout(pad = 0)
ax.axis('off')
ax.axis('equal')

# Set bounds
xmin, ymin, xmax, ymax = unary_union([all_shapes, shadow]).bounds
pad = .1
ax.set_xlim(xmin - pad, xmax + pad)
ax.set_ylim(ymin + pad, ymax + pad)

# Create pattern
n = 64
x, y = np.meshgrid(np.linspace(xmin, xmax, n), np.linspace(ymin, ymax, n))
i, j = np.meshgrid(np.arange(n), np.arange(n))
r = norm(np.stack([x-(xmin+xmax)/2, y-(ymin+ymax)/2], axis = -1), axis = -1)
i, j, x, y, r = map(lambda a: a.reshape(-1).tolist(), [i, j, x, y, r])
background_pattern = rotate(unary_union([
    circle(
        (x, y if i % 2 == 0 else y + (ymax-ymin)/(2*n)),
        r = (1/n) * np.exp(-.1*r**2)
    )
    for i, j, x, y, r in zip(i, j, x, y, r)
    if r < .5*(xmax-xmin) + .2*randn()
]), 15).difference(all_shapes)

# Plot shapes
for shape in shapes:
    for patch in shape2patches(shape, ec = 'black', fc = choice(palette), lw = 6):
        ax.add_patch(patch)
# Plot shadow
for shape in shadow:
    for patch in shape2patches(shape, ec = 'black', fc = 'black', lw = 3):
        ax.add_patch(patch)
# Plot pattern
for shape in background_pattern:
    for patch in shape2patches(shape, ec = 'black', fc = 'black', lw = 3):
        ax.add_patch(patch)

fig.patch.set_facecolor('#ECECD4')

plt.savefig('prints/ribbons.png', format = 'png')
plt.show()

# Vsketch

In [4]:
import vsketch

class Sketch(vsketch.Vsketch):
    
    # Sketch parameters:
    n = vsketch.Param(9)

    def draw(self) -> None:

        self.size("a4", landscape = False)
        self.scale("cm")
        self.scale(2.9, -2.9)

        shapes_ = [
            shape.difference(unary_union(shapes[i+1:]))
            for i, shape in enumerate(shapes)
        ]

        for shape in shapes_:
            self.stroke(1)
            self.strokeWeight(4)
            #self.fill(randint(2, 4))
            self.geometry(shape)

        for shape in shadow:
            self.stroke(1)
            self.strokeWeight(2)
            self.fill(1)
            self.geometry(shape)

        for shape in background_pattern.difference(shadow):
            self.stroke(1)
            self.strokeWeight(2)
            self.fill(1)
            self.geometry(shape)

    def finalize(self) -> None:
        self.vpype("linemerge linesimplify reloop linesort")


vsk = Sketch()
vsk.draw()
vsk.finalize()

vsk.display()
vsk.save('prints/ribbons-plotter.svg')

<?xml version="1.0" encoding="utf-8" ?>
 
 
 
 
 image/svg+xml 
 
 2021-04-09T10:15:12.610075 
 
 
 
 
 
 
 
 
 <polygon points="159.0864,456.3985 150.5129,462.6133 142.5897,469.6385 135.3933,477.4065 128.993,485.8425 123.4503,494.8652 118.8187,504.3877 115.1428,514.3183 112.458,524.5615 110.79,535.0184 110.1551,545.5885 110.5609,556.2117 120.1101,665.3593 119.9572,666.2263 119.3913,666.9008 118.564,667.2019 74.8883,671.023 74.0213,670.8701 73.3469,670.3042 73.0458,669.4769 63.4929,560.2877 63.079,549.2891 63.7239,538.5522 65.4363,527.7643 68.1979,517.1962 71.982,506.9496 76.7522,497.1234 82.5569,487.6742 89.1655,478.9772 96.4755,471.0866 104.7731,463.7294 113.6218,457.3253 123.0556,451.8194 132.8287,447.3268 143.15,443.7516 153.936,441.1746 164.7587,439.6979 175.5072,439.2873 187.1518,440.0464 187.9712,440.4344 188.5267,441.3965 188.4453,442.327 187.7312,443.178 177.8492,446.6312 168.2279,451.054"/>
 
 
 
 
 
 
 
 
 <polygon points="208.5488,438.1418 197.9476,439.5963 189.6203,441.5859 197.0747,442.7777 207.5325,445.5216 217.6199,449.2555 227.3438,453.9821 236.5577,459.6389 245.1727,466.1717 253.1448,473.5572 260.3157,481.6488 266.6286,490.3577 272.1136,499.7393 276.6061,509.5124 280.1398,519.7305 282.655,530.2457 284.054,540.422 326.5988,536.6998 325.2214,526.661 322.7347,516.2533 319.2399,506.1396 314.7707,496.4171 309.3699,487.1794 303.0897,478.5157 295.9906,470.5092 288.1409,463.2371 279.6162,456.7694 270.4985,451.1684 260.8758,446.4881 250.8407,442.7735 240.4898,440.0604 229.9229,438.3749 219.2416,437.7333"/>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polyline points="198.9555,450.1849 213.5979,450.1849 216.6611,451.3187 189.7763,451.3187 190.0067,453.5864 221.3458,453.5864 223.677,454.7203 194.3326,454.7203 198.1414,455.8542 226.0082,455.8542 227.9099,456.988 201.2046,456.988 204.2677,458.1219 229.7557,458.1219 231.6014,459.2557 207.2832,459.2557 209.6144,460.3896 233.4472,460.3896 235.293,461.5234 211.9456,461.5234 214.2768,462.6573 236.7887,462.6573 235.815,463.7912 216.608,463.7912 218.5259,464.925 234.2508,464.925 232.5293,466.0589 220.3716,466.0589 222.2174,467.1927 230.5899,467.1927 228.6505,468.3266 224.0632,468.3266 225.9089,469.4604 226.7111,469.4604"/>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <polyline points="284.3704,813.0059 284.1298,813.0059 284.6414,814.1398 275.4174,814.1398 275.573,815.2737 284.9123,815.2737 285.1832,816.4075 275.7286,816.4075 275.8842,817.5414 285.4541,817.5414 285.725,818.6752 276.0397,818.6752 276.1953,819.8091 285.9959,819.8091 286.2668,820.943 276.3509,820.943 276.5064,822.0768 286.5377,822.0768 286.8451,823.2107 276.7265,823.2107 276.9974,824.3445 287.2369,824.3445 287.6287,825.4784 277.2683,825.4784 277.5392,826.6122 288.0206,826.6122 288.4124,827.7461 277.8102,827.7461 278.0811,828.88 288.8042,828.88 289.196,830.0138 278.352,830.0138 278.6229,831.1477 289.5878,831.1477 289.9796,832.2815 278.8938,832.2815 279.2222,833.4154 290.3968,833.4154 290.918,834.5493 279.614,834.5493 280.0058,835.6831 291.4393,835.6831 291.9605,836.817 280.3976,836.817 280.7895,837.9508 292.4817,837.9508 293.0029,839.0847 281.1813,839.0847 281.5731,840.2185 293.5241,840.2185 294.0453,841.3524 281.9649,841.3524 282.3567,842.4863 294.5666,842.4863 295.1506,843.6201 282.8325,843.6201 283.3537,844.754 295.8135,844.754 296.4764,845.8878 283.8749,845.8878 284.3961,847.0217 297.1393,847.0217 297.8022,848.1556 284.9173,848.1556 285.4386,849.2894 298.4651,849.2894 299.128,850.4233